Multiple linear regression example
===

Assume the model
$$
\mathbf{y} = X \boldsymbol{\beta} + \boldsymbol{\epsilon}.
$$
Under the constraint of minimizing the sum of squared residuals, the solution is 
obtained by solving the *normal equations*
$$
(X^TX)\boldsymbol{\beta} = X^T\mathbf{y}.
$$

The naive implementation would use the inverse of the matrix $(X^TX),$ while better ones would resort to more 
robust algorithms.

In [1]:
import numpy as np
import scipy

In [2]:
X = np.array([
    [1, 1, 2],
    [1, 2.01, 4],
    [1, 3.01, 6],
    [1, 4.01, 8],
    [1, 5.01, 10]
])

y = np.array([1, 2, 3, 4, 5])

# Attempting to solve the normal equations directly
try:
    beta_hat_direct = np.linalg.inv(X.T @ X) @ X.T @ y   # '@' is equiv. to np.matmul() 
    print("Beta coefficients using inverse:", beta_hat_direct)
except np.linalg.LinAlgError as e:
    print(f"Error in direct inversion: {e}")

# Solving using np.linalg.solve()
beta_hat_solve = np.linalg.solve(X.T @ X, X.T @ y)

print("Beta coefficients using np.linalg.solve():", beta_hat_solve)

Beta coefficients using inverse: [-3.48229889e-10 -6.18456397e-11  5.00000000e-01]
Beta coefficients using np.linalg.solve(): [0.  0.  0.5]


In [3]:
A = np.array([[1,2],[3,4]])
b = np.array([-1, -1])
x_0 = np.array([1,-1])  # exact solution

print("A x = ", A @ x_0)
print("b = ", b)

try:
    x_direct = np.linalg.inv(A) @ b
    print("x using inverse:", x_direct)
except np.linalg.LinAlgError as e:
    print(f"Error in direct inversion: {e}")

try:
    x_1 = np.linalg.solve(A, b)
    print("x using np.linalg.solve():", x_1)
except np.linalg.LinAlgError as e:
    print(f"Error in solve(): {e}")

try:
    x_2 = np.linalg.lstsq(A, b, rcond=None)
    print("x using np.linalg.lstsq():", x_2)
except np.linalg.LinAlgError as e:
    print(f"Error in lstsq(): {e}")


A x =  [-1 -1]
b =  [-1 -1]
x using inverse: [ 1. -1.]
x using np.linalg.solve(): [ 1. -1.]
x using np.linalg.lstsq(): (array([ 1., -1.]), array([], dtype=float64), 2, array([5.4649857 , 0.36596619]))


In [4]:
A = np.array([[1,2],[2,4]])
b = np.array([-1, -2])
x_0 = np.array([1,-1])  # one possible solution

print("A x = ", A @ x_0)
print("b = ", b)

try:
    x_direct = np.linalg.inv(A) @ b
    print("x using inverse:", x_direct)
except np.linalg.LinAlgError as e:
    print(f"Error in direct inversion: {e}")

try:
    x_1 = np.linalg.solve(A, b)
    print("x using np.linalg.solve():", x_1)
except np.linalg.LinAlgError as e:
    print(f"Error in solve(): {e}")

try:
    x_2 = np.linalg.lstsq(A, b, rcond=None)
    print("x using np.linalg.lstsq():", x_2)
except np.linalg.LinAlgError as e:
    print(f"Error in lstsq(): {e}")


A x =  [-1 -2]
b =  [-1 -2]
Error in direct inversion: Singular matrix
Error in solve(): Singular matrix
x using np.linalg.lstsq(): (array([-0.2, -0.4]), array([], dtype=float64), 1, array([5.00000000e+00, 1.98602732e-16]))


Hilbert matrices
===

$$
H_{ij} = \int_0^1 x^{i+j} dx = \frac{1}{i+j-1}, \quad i, j \geq 1
$$

Pay attention, in Python indices start at 0!

In [9]:
for n in np.arange(5, 15):
    H = scipy.linalg.hilbert(n)
    invH = scipy.linalg.invhilbert(n) # exact inverse for n < 15!
    c  = np.linalg.cond(H)
    d1 = np.linalg.det(H) * np.linalg.det(np.linalg.inv(H))
    d2 = np.linalg.det(H) * np.linalg.det(invH)
    print('n={:2d}\tcond={:e}\tdet1={:10.7f}\t\tdet2={:10.7f}'.format(n, c, d1, d2))

n= 5	cond=4.766073e+05	det1= 1.0000000		det2= 1.0000000
n= 6	cond=1.495106e+07	det1= 1.0000000		det2= 1.0000000
n= 7	cond=4.753674e+08	det1= 1.0000000		det2= 1.0000000
n= 8	cond=1.525758e+10	det1= 1.0000000		det2= 1.0000000
n= 9	cond=4.931542e+11	det1= 0.9999988		det2= 1.0000032
n=10	cond=1.602533e+13	det1= 1.0000046		det2= 1.0001044
n=11	cond=5.225086e+14	det1= 1.0012569		det2= 1.0026542
n=12	cond=1.802293e+16	det1= 0.9958001		det2= 1.0882269
n=13	cond=1.667719e+18	det1= 0.8764014		det2= 3.6355167
n=14	cond=5.131726e+17	det1= 3.2869106		det2=90.9378779


Solving linear systems with square $A$
===

Diagonal A
--

In [6]:
def diagsolve(A, b):
    # Solve A x = b for a diagonal matrix A.
    d = np.diag(A)
    if np.any(np.isclose(d, 0)) :
        raise RuntimeError('A is singular!')
    x = b / d   # this is element-wise

    return x

In [7]:
A = np.array([[1, 0, 0], [0, 2, 0],[0, 0, 3]])
# try:
# A = np.array([[1, 0, 0], [0, 2e-16, 0],[0, 0, 3]])
b = np.array([1, 2, 3])
print(diagsolve(A, b))

[1. 1. 1.]


LU factorization
--

In [8]:
A = np.array([[0, 1, 1], [2, -1, -1], [1, 1, -1]]) 
b = np.array([2, 0, 1])
res = scipy.linalg.lu(A)  # check the documentation!
L = res[1]
U = res[2]
y = scipy.linalg.solve_triangular(L, b, lower=True)
x = scipy.linalg.solve_triangular(U, y, lower=False)
print(x)

[ 1.5  -0.25  1.25]
